# PRACTICUM 1

## EINDOPDRACHT

In [1]:
from ipywidgets import *
import ipywidgets as widgets
from fractions import Fraction
from sympy import *
import numpy as np
from scipy.integrate import odeint
import matplotlib.pyplot as plt


import plotly as py 
import plotly.graph_objs as go 
py.offline.init_notebook_mode(connected=True)


De eerst orde differentiaalvergelijking is:

$$
a \cdot \dfrac{dy}{dx} + b\cdot y = c \cdot x
$$

## Analytische Oplossing

In [2]:
a = 1
b = -3
c = 4

In [3]:
def dy_dx(y,x):
        return y*3*x**2*np.sin(x**3) 

De eerst orde differentiaalvergelijking is:

In [4]:
x, y, z, dy, dx, C, expo = symbols('x y z dy dx C e')
#glue("sym_eq", Integral(sqrt(1/x)+a, x))
display(Eq(a*dy/dx, y*3*x**2*sin(x**3)))

Eq(dy/dx, 3*x**2*y*sin(x**3))

In [5]:
display(Eq(dy/dx, Fraction(c,a)*x+Fraction(b,a)*y))

Eq(dy/dx, 4*x - 3*y)

De beginvoorwaarde is:

In [6]:
y0 = 3

De algemene oplossing is:

$$
y = Ce^{A1 \cdot x}+A2\cdot x + A3
$$


In [7]:
A1 = 1-cos(x**3)
A2 = 0
A3 = 0

In [8]:
C = 3

In [9]:
display(Eq(y,simplify(C*expo**(A1))+nsimplify(A2)*x+nsimplify(A3)))

Eq(y, 3*e**(1 - cos(x**3)))

In [10]:
def odeint_oplossing(ode_func, y0, t):
    y = odeint(ode_func, y0, t)
    return y

In [11]:
def analytische_oplossing(x):
    return 3*np.exp(1-np.cos(x**3))

In [12]:
# Generate a grid of x,y values
x = np.linspace(-20, 20, 200)
y = np.linspace(-20, 20, 200)

X, Y = np.meshgrid(x, y)
U = 1  # Constant unit vector for slope field
V = dy_dx(Y, X)

# Normalize the arrow length
N = np.sqrt(U**2 + V**2)
U = U / N
V = V / N

In [13]:
x_current = np.linspace(0,10,10000)
y_values = analytische_oplossing(x_current)

# Plot het richtingsveld
def interactive_plot(xmin=0, xmax=3, ymin=-3, ymax=10, y0=y0):
    plt.figure(figsize=(10,6))
    
    plt.quiver(X, Y, U, V, angles='xy', scale_units='xy', scale=5, color='blue')
    
    y_an = odeint_oplossing(dy_dx, y0, x_current) 
    #plt.plot(x_current, y_an, "c-")
    
    plt.plot(x_current, y_values, "r-")
    
    plt.xlabel('X-axis')
    plt.xlim(xmin, xmax)
    plt.ylim(ymin,ymax)
    plt.ylabel('Y-axis')
    plt.title('Richtingsveld')
    plt.grid(True)
    plt.show()
 
 
interact(interactive_plot, xmin=(-10, 0, 1), xmax=(0, 10, 1), ymin=(-10, 0, 1), ymax=(0, 10, 1), y0=(-10, 10, 0.5))

interactive(children=(IntSlider(value=0, description='xmin', max=0, min=-10), IntSlider(value=3, description='…

<function __main__.interactive_plot(xmin=0, xmax=3, ymin=-3, ymax=10, y0=3)>

<HR>

## Euler voorwaarts Methode

De functie $y(x)$ kan formeel gezien als volgt bepaald worden:

$$
y(x) = y(x_0) + \int y'(t)dt = y(x_0) + \int f(t, y(t))dt
$$


Deze integraal is over het algemeen niet analytisch te bepalen. Een methode om deze integraal te benaderen is om de waarde van de integraal te benaderen met de waarde van $f(t,y(t))$ aan het begin van het interval keer de breedte van het interval. Dit geeft de volgende benadering:

$$
y(x) = y(x_0) + (x-x_0)f(x_0 y(x_0))
$$

Logisch is dat deze benadering voor $x$ ver van $x_0$ niet betrouwbaar zal zijn. Daarom wordt gekozen om voor de benadering op een interval dit interval in kleine stappen met grootte $h$ te verdelen en vervolgens deze formule achtereenvolgens op de verschillende punten toe te passen. De benadering in punt $i$ wordt vaak genoteerd als $w_i$. De recursieve formule voor Euler voorwaarts is:

$$
w_{n+1} = w_n + h \cdot f(x_n, w_n)
$$


In [14]:
def euler_voorwaarts_methode(dy_dx, y0, x):
    y = np.zeros_like(x)
    y[0]=y0
    
    for i in range(1,len(x)):
        h = x[i] - x[i-1]
        y[i] = y[i-1]+ h * dy_dx(y[i-1], x[i-1]) 
    return y

In [15]:
# minimaal 2 waardes invullen, dit mogen dezelfde zijn.
euler_voorwaarts_stapgrootte1 = 0.1
euler_voorwaarts_stapgrootte2 = 0.2

In [16]:
x_euler_voorwaarts1 = np.arange(0, 10+euler_voorwaarts_stapgrootte1,euler_voorwaarts_stapgrootte1)
y_euler_voorwaarts1 = euler_voorwaarts_methode(dy_dx, y0, x_euler_voorwaarts1) 

x_euler_voorwaarts2 = np.arange(0, 10+euler_voorwaarts_stapgrootte2,euler_voorwaarts_stapgrootte2)
y_euler_voorwaarts2 = euler_voorwaarts_methode(dy_dx, y0, x_euler_voorwaarts2) 

In [17]:
layout = go.Layout(
    title={'text': 'Analytische oplossing vs Euler voorwaarts'},
    xaxis = dict(
        title = 'x-as',
        range = [0,2.5] ),
    yaxis = dict(
        title = 'y-as',
        range = [0,30] ),
)

line = go.Scatter(
    x = x_current,
    y = y_values,
    mode = 'lines',
    name = 'analytische oplossing',
    line_color= 'red',
)

line2 = go.Scatter(
    x = x_euler_voorwaarts1,
    y = y_euler_voorwaarts1,
    mode = 'markers',
    name = 'euler '+str(euler_voorwaarts_stapgrootte1),
    line_color= 'green',
)

line3 = go.Scatter(
    x = x_euler_voorwaarts2,
    y = y_euler_voorwaarts2,
    mode = 'markers',
    name = 'euler '+str(euler_voorwaarts_stapgrootte2),
    line_color= 'blue',
)

fig = go.Figure(data=[ line, line2, line3], layout=layout)

py.offline.iplot(fig)

<HR>

## Modified Euler Methode

De functie $y(x)$ kan formeel gezien als volgt bepaald worden:

$$
y(x) = y(x_0) + \int y'(t)dt = y(x_0) + \int f(t, y(t))dt
$$

Bij Euler voorwaarts wordt de integraal benaderd met behulp van de waarde van $f(x,y)$ in het punt $(x_n,w_n)$. De benadering van de integraal zou nauwkeuriger zijn als de waarde van $f(x_{n+1}, w_{n+1})$ ook gebruikt zou worden, bijvoorbeeld door de trapeziumregel toe te passen:

$$
w_{n+1} = w_n + \dfrac{h}{2} \left( f(x_n, w_n) + f(x_{n+1}, w_{n+1}) \right)
$$

Dit is een impliciete formule die niet direct is toe te passen. Modified Euler is gebaseerd op deze regel, maar dan expliciet gemaakt. De onbekende waarde wn+1 aan de rechterzijde van de vergelijking wordt eerst geschat, dit wordt de predictor genoemd. Dit geeft de volgende recursieve formules:

$$
\bar{w}_{n+1} = w_n + h \cdot f(x_n, w_n)
$$

$$
w_{n+1} = w_n + \dfrac{h}{2} \left( f(x_n, w_n) + f(x_{n+1}, \bar{w}_{n+1}) \right)
$$



In [18]:
def modified_euler_methode(ode_func, y0, x):
    y = np.zeros_like(x)
    y[0] = y0

    for i in range(1, len(x)):
        h = x[i] - x[i-1]

        # Predict using Euler's method
        y_predictor = y[i-1] + h * ode_func(y[i-1], x[i-1]) 

        # Correct using the average slope
        y[i] = y[i-1] + 0.5 * (ode_func(y[i-1], x[i-1]) + ode_func(y_predictor, x[i])) * h

    return y

In [19]:
# minimaal 2 waardes invullen, dit mogen dezelfde zijn.
euler_modified_stapgrootte1 = 0.1
euler_modified_stapgrootte2 = 0.2

In [20]:

x_modified_euler1 = np.arange(0, 10+euler_modified_stapgrootte1,euler_modified_stapgrootte1)
y_modified_euler1 = modified_euler_methode(dy_dx, y0, x_modified_euler1)

x_modified_euler2 = np.arange(0, 10+euler_modified_stapgrootte2,euler_modified_stapgrootte2)
y_modified_euler2 = modified_euler_methode(dy_dx, y0, x_modified_euler2) 

In [21]:
layout = go.Layout(
    title={'text': 'Analytische oplossing vs Euler voorwaarts vs Modified Euler'},
    xaxis = dict(
        title = 'x-as',
        range = [0,2.5] ),
    yaxis = dict(
        title = 'y-as',
        range = [0,30] ),
)

line = go.Scatter(
    x = x_current,
    y = y_values,
    mode = 'lines',
    name = 'analytische oplossing',
    line_color= 'red',
)

line2 = go.Scatter(
    x = x_euler_voorwaarts1,
    y = y_euler_voorwaarts1,
    mode = 'markers',
    name = 'euler '+str(euler_voorwaarts_stapgrootte1),
    line_color= 'green',
)

line3 = go.Scatter(
    x = x_euler_voorwaarts2,
    y = y_euler_voorwaarts2,
    mode = 'markers',
    name = 'euler '+str(euler_voorwaarts_stapgrootte2),
    line_color= 'blue',
)

line4 = go.Scatter(
    x = x_modified_euler1,
    y = y_modified_euler1,
    marker = dict(
            size=10,
            symbol ="star",
            color='green',
            ),
    mode = 'markers',
    name = 'euler modified '+str(euler_modified_stapgrootte1),
    line_color= 'yellow',
)

line5 = go.Scatter(
    x = x_modified_euler2,
    y = y_modified_euler2,
    marker = dict(
            size=10,
            symbol ="star",
            color='blue',
            ),
    mode = 'markers',
    name = 'euler modified '+str(euler_modified_stapgrootte2),
    line_color= 'brown',
)


fig = go.Figure(data=[ line, line2, line3, line4, line5], layout=layout)

py.offline.iplot(fig)